### Imports for strategy

In [1]:
from collections import deque
from datetime import timedelta
from typing import Dict

from nautilus_trader.core.message import Event
from nautilus_trader.common.functions import fast_mean
from nautilus_trader.model.enums import OrderSide, OrderPurpose, TimeInForce, Currency, SecurityType
from nautilus_trader.model.objects import Price, Tick, BarSpecification, BarType, Bar, Instrument
from nautilus_trader.model.identifiers import Symbol
from nautilus_trader.model.events import OrderRejected
from nautilus_trader.trade.strategy import TradingStrategy
from nautilus_trader.trade.sizing import FixedRiskSizer

from nautilus_indicators.average.ema import ExponentialMovingAverage
from nautilus_indicators.atr import AverageTrueRange
from nautilus_indicators.__info__ import __version__ as n_indicators_version

print(f'nautilus_indicators {n_indicators_version}')

nautilus_indicators 0.62.2


In [2]:
class EMACrossPy(TradingStrategy):
    """"
    A simple moving average cross example strategy. When the fast EMA crosses
    the slow EMA then a STOP_MARKET atomic order is placed for that direction
    with a trailing stop and profit target at 1R risk.
    """

    def __init__(self,
                 symbol: Symbol,
                 bar_spec: BarSpecification,
                 risk_bp: float=10.0,
                 fast_ema: int=10,
                 slow_ema: int=20,
                 atr_period: int=20,
                 sl_atr_multiple: float=2.0):
        """
        Initializes a new instance of the EMACrossPy class.

        :param symbol: The symbol for the strategy.
        :param bar_spec: The bar specification for the strategy.
        :param risk_bp: The risk per trade (basis points).
        :param fast_ema: The fast EMA period.
        :param slow_ema: The slow EMA period.
        :param atr_period: The ATR period.
        :param sl_atr_multiple: The ATR multiple for stop-loss prices.
        """
        # Order id tag must be unique at trader level
        super().__init__(order_id_tag=symbol.code, bar_capacity=40)

        # Custom strategy variables
        self.symbol = symbol
        self.bar_type = BarType(symbol, bar_spec)
        self.precision = 5          # dummy initial value for FX
        self.risk_bp = risk_bp
        self.entry_buffer = 0.0     # instrument.tick_size
        self.SL_buffer = 0.0        # instrument.tick_size * 10
        self.SL_atr_multiple = sl_atr_multiple

        self.instrument = None      # initialized in on_start()
        self.position_sizer = None  # initialized in on_start()

        # Track spreads
        self.spreads = deque(maxlen=100)

        # Create the indicators for the strategy
        self.fast_ema = ExponentialMovingAverage(fast_ema)
        self.slow_ema = ExponentialMovingAverage(slow_ema)
        self.atr = AverageTrueRange(atr_period)

        # Register the indicators for updating
        self.register_indicator(data_source=self.bar_type, indicator=self.fast_ema, update_method=self.fast_ema.update)
        self.register_indicator(data_source=self.bar_type, indicator=self.slow_ema, update_method=self.slow_ema.update)
        self.register_indicator(data_source=self.bar_type, indicator=self.atr, update_method=self.atr.update)

    def on_start(self):
        """
        This method is called when self.start() is called, and after internal start logic.
        """
        # Put custom code to be run on strategy start here (or pass)
        self.instrument = self.get_instrument(self.symbol)
        self.precision = self.instrument.tick_precision
        self.entry_buffer = self.instrument.tick_size.as_double() * 3.0
        self.SL_buffer = self.instrument.tick_size * 10.0
        self.position_sizer = FixedRiskSizer(self.instrument)

        self.request_bars(self.bar_type)
        self.subscribe_instrument(self.symbol)
        self.subscribe_bars(self.bar_type)
        self.subscribe_ticks(self.symbol)

    def on_tick(self, tick: Tick):
        """
        This method is called whenever a Tick is received by the strategy, and
        after the Tick has been processed by the base class.
        The received Tick object is then passed into this method.

        :param tick: The received tick.
        """
        # self.log.info(f"Received Tick({tick})")  # For demonstration purposes
        self.spreads.append(tick.ask.as_double() - tick.bid.as_double())

    def on_bar(self, bar_type: BarType, bar: Bar):
        """
        This method is called whenever the strategy receives a Bar, and after the
        Bar has been processed by the base class.
        The received BarType and Bar objects are then passed into this method.

        :param bar_type: The received bar type.
        :param bar: The received bar.
        """
        # self.log.info(f"Received {bar_type} Bar({bar})")  # For demonstration purposes

        # Check if indicators ready
        if not self.indicators_initialized():
            return  # Wait for indicators to warm up...

        # Check if tick data available
        if not self.has_ticks(self.symbol):
            return  # Wait for ticks...

        # Calculate average spread
        average_spread = fast_mean(self.spreads)

        # Check market liquidity
        if average_spread == 0.0:
            return  # Protect divide by zero
        else:
            liquidity_ratio = self.atr.value / average_spread
            if liquidity_ratio < 2.0:
                self.log.info(f"Liquidity Ratio == {liquidity_ratio} (no liquidity).")
                return

        if self.count_orders_working() == 0 and self.is_flat():  # No active or pending positions
            atomic_order = None

            # BUY LOGIC
            if self.fast_ema.value >= self.slow_ema.value:
                price_entry = Price(bar.high + self.entry_buffer + max(average_spread, self.spreads[-1]), self.precision)
                price_stop_loss = Price(bar.low - (self.atr.value * self.SL_atr_multiple), self.precision)
                price_take_profit = Price(price_entry + (price_entry.as_double() - price_stop_loss.as_double()), self.precision)

                if self.instrument.security_type == SecurityType.FOREX:
                    quote_currency = Currency[self.instrument.symbol.code[3:]]
                    exchange_rate = self.xrate_for_account(quote_currency)
                else:
                    exchange_rate = self.xrate_for_account(self.instrument.base_currency)

                position_size = self.position_sizer.calculate(
                    equity=self.account().free_equity,
                    risk_bp=self.risk_bp,
                    price_entry=price_entry,
                    price_stop_loss=price_stop_loss,
                    exchange_rate=exchange_rate,
                    commission_rate_bp=0.15,
                    hard_limit=20000000,
                    units=1,
                    unit_batch_size=10000)
                if position_size.value > 0:
                    atomic_order = self.order_factory.atomic_stop_market(
                        symbol=self.symbol,
                        order_side=OrderSide.BUY,
                        quantity=position_size,
                        price_entry=price_entry,
                        price_stop_loss=price_stop_loss,
                        price_take_profit=price_take_profit,
                        time_in_force=TimeInForce.GTD,
                        expire_time=bar.timestamp + timedelta(minutes=1))
                else:
                    self.log.info("Insufficient equity for BUY signal.")

            # SELL LOGIC
            elif self.fast_ema.value < self.slow_ema.value:
                price_entry = Price(bar.low - self.entry_buffer, self.precision)
                price_stop_loss = Price(bar.high + (self.atr.value * self.SL_atr_multiple) + max(average_spread, self.spreads[-1]), self.precision)
                price_take_profit = Price(price_entry - (price_stop_loss.as_double() - price_entry.as_double()), self.precision)

                if self.instrument.security_type == SecurityType.FOREX:
                    quote_currency = Currency[self.instrument.symbol.code[3:]]
                    exchange_rate = self.xrate_for_account(quote_currency)
                else:
                    exchange_rate = self.xrate_for_account(self.instrument.base_currency)

                position_size = self.position_sizer.calculate(
                    equity=self.account().free_equity,
                    risk_bp=self.risk_bp,
                    price_entry=price_entry,
                    price_stop_loss=price_stop_loss,
                    exchange_rate=exchange_rate,
                    commission_rate_bp=0.15,
                    hard_limit=20000000,
                    units=1,
                    unit_batch_size=10000)

                if position_size.value > 0:  # Sufficient equity for a position
                    atomic_order = self.order_factory.atomic_stop_market(
                        symbol=self.symbol,
                        order_side=OrderSide.SELL,
                        quantity=position_size,
                        price_entry=price_entry,
                        price_stop_loss=price_stop_loss,
                        price_take_profit=price_take_profit,
                        time_in_force=TimeInForce.GTD,
                        expire_time=bar.timestamp + timedelta(minutes=1))
                else:
                    self.log.info("Insufficient equity for SELL signal.")

            # ENTRY ORDER SUBMISSION
            if atomic_order:
                self.submit_atomic_order(atomic_order, self.position_id_generator.generate())

        for working_order in self.orders_working().values():
            # TRAILING STOP LOGIC
            if working_order.purpose == OrderPurpose.STOP_LOSS:
                # SELL SIDE ORDERS
                if working_order.is_sell:
                    temp_price = Price(bar.low - (self.atr.value * self.SL_atr_multiple), self.precision)
                    if temp_price > working_order.price:
                        self.modify_order(working_order, working_order.quantity, temp_price)
                # BUY SIDE ORDERS
                elif working_order.is_buy:
                    temp_price = Price(bar.high + (self.atr.value * self.SL_atr_multiple) + max(average_spread, self.spreads[-1]), self.precision)
                    if temp_price < working_order.price:
                        self.modify_order(working_order, working_order.quantity, temp_price)

    def on_instrument(self, instrument: Instrument):
        """
        This method is called whenever the strategy receives an Instrument update.

        :param instrument: The received instrument.
        """
        if self.instrument.symbol.equals(instrument.symbol):
            self.instrument = instrument

        self.log.info(f"Updated instrument {instrument}.")

    def on_event(self, event: Event):
        """
        This method is called whenever the strategy receives an Event object,
        and after the event has been processed by the TradingStrategy base class.
        These events could be AccountEvent, OrderEvent, PositionEvent, TimeEvent.

        :param event: The received event.
        """
        # Put custom code for event handling here (or pass)
        if isinstance(event, OrderRejected):
            position = self.position_for_order(event.order_id)
            if position is not None and position.is_open:
                self.flatten_position(position.id)

    def on_stop(self):
        """
        This method is called when self.stop() is called and after internal
        stopping logic.
        """
        # Put custom code to be run on strategy stop here (or pass)
        pass

    def on_reset(self):
        """
        This method is called when self.reset() is called, and after internal
        reset logic such as clearing the internally held bars, ticks and resetting
        all indicators.
        """
        # Put custom code to be run on a strategy reset here (or pass)
        pass

    def on_save(self) -> Dict:
        # Put custom state to be saved here (or return empty dictionary)
        return {}

    def on_load(self, state: Dict):
        # Put custom state to be loaded here (or pass)
        pass

    def on_dispose(self):
        """
        This method is called when self.dispose() is called. Dispose of any
        resources that has been used by the strategy here.
        """
        # Put custom code to be run on a strategy disposal here (or pass)
        self.unsubscribe_instrument(self.symbol)
        self.unsubscribe_bars(self.bar_type)
        self.unsubscribe_ticks(self.symbol)


### Get Data

In [8]:
import sys
import pytz

from datetime import datetime

from nautilus_research.__info__ import __version__ as nautilus_research_version
from nautilus_research.database import ResearchDatabaseClient, Database, Library, MarketDataType
from nautilus_research.data.integrity import check_tick_data

print(f'nautilus_research {nautilus_research_version}')

nautilus_research 0.66.2


In [11]:
library = ResearchDatabaseClient(database=Database.MARKET_DATA)(Library.FXCM)

start = datetime(2017, 1, 1, 0, 0, 0, 0, pytz.UTC)
stop = datetime(2017, 12, 1, 0, 0, 0, 0, pytz.UTC)

tick_data = library.read_ticks(
        symbol='AUDUSD',
        start_datetime=start,
        end_datetime=stop)

print(f'{tick_data.shape[0]:,} rows {sys.getsizeof(tick_data):,}')
tick_data.head()

42,409,839 rows 1,017,836,168


bid      ask
timestamp                                         
2017-01-03 00:00:00.014000+00:00  0.71956  0.71962
2017-01-03 00:00:00.032000+00:00  0.71958  0.71962
2017-01-03 00:00:00.039000+00:00  0.71956  0.71962
2017-01-03 00:00:00.313000+00:00  0.71956  0.71961
2017-01-03 00:00:00.321000+00:00  0.71955  0.71961

### Build Backtest Engine

In [5]:
from nautilus_trader.common.logger import LogLevel
from nautilus_trader.model.enums import BarStructure, Currency, PriceType
from nautilus_trader.model.identifiers import Venue, TraderId
from nautilus_trader.backtest.config import BacktestConfig
from nautilus_trader.backtest.data import BacktestDataContainer
from nautilus_trader.backtest.models import FillModel
from nautilus_trader.backtest.engine import BacktestEngine
from nautilus_trader.backtest.loaders import InstrumentLoader

from nautilus_trader.__info__ import __version__ as n_trader_version
print(f'nautilus_trader {n_trader_version}')

nautilus_trader 1.12.3


In [6]:
loader = InstrumentLoader()
AUDUSD = loader.default_fx_ccy(Symbol('AUDUSD', Venue('FXCM')), tick_precision=5)  # Test Instrument

data = BacktestDataContainer()
data.add_instrument(AUDUSD)
data.add_ticks(AUDUSD.symbol, tick_data)

strategies = [EMACrossPy(
    symbol=AUDUSD.symbol,
    bar_spec=BarSpecification(200, BarStructure.TICK, PriceType.MID),
    risk_bp=10,
    fast_ema=10,
    slow_ema=20,
    atr_period=20,
    sl_atr_multiple=2.0)]

config = BacktestConfig(
    exec_db_type='in-memory',
    exec_db_flush=False,
    frozen_account=False,
    starting_capital=1000000,
    account_currency=Currency.USD,
    bypass_logging=False,
    level_console=LogLevel.INFO,
    level_file=LogLevel.DEBUG,
    level_store=LogLevel.WARNING,
    log_thread=False,
    log_to_file=False)

fill_model = FillModel(
    prob_fill_at_limit=0.2,
    prob_fill_at_stop=0.95,
    prob_slippage=0.5,
    random_seed=None)

engine = BacktestEngine(
    data=data,
    strategies=strategies,
    config=config,          # Optional (can be None)
    fill_model=fill_model)  # Optional (can be None)

2020-01-17 04:27:51.389Z [INF] BacktestEngine: #---------------------------------------------------------------#
2020-01-17 04:27:51.389Z [INF] BacktestEngine:  Nautilus Trader - Algorithmic Trading Platform
2020-01-17 04:27:51.389Z [INF] BacktestEngine:  by Nautech Systems Pty Ltd. 
2020-01-17 04:27:51.389Z [INF] BacktestEngine:  Copyright (C) 2015-2020. All rights reserved.
2020-01-17 04:27:51.389Z [INF] BacktestEngine: #---------------------------------------------------------------#
2020-01-17 04:27:51.389Z [INF] BacktestEngine:                                                                  
2020-01-17 04:27:51.389Z [INF] BacktestEngine:                             .......                              
2020-01-17 04:27:51.390Z [INF] BacktestEngine:                          .............                           
2020-01-17 04:27:51.390Z [INF] BacktestEngine:     .                  ......... .......                         
2020-01-17 04:27:51.390Z [INF] BacktestEngine:    .     

In [12]:
help(engine.run)

Help on built-in function run:

run(...) method of nautilus_trader.backtest.engine.BacktestEngine instance
    BacktestEngine.run(self, datetime start=None, datetime stop=None, FillModel fill_model=None, list strategies=None, bool print_log_store=True) -> void
    File: nautilus_trader/backtest/engine.pyx (starting at line 177)
    
            Run a backtest from the start datetime to the stop datetime.
            Note: If start datetime is None will run from the start of the data.
            Note: If stop datetime is None will run to the end of the data.
    
            :param start: The optional start datetime (UTC) for the backtest run.
            :param stop: The optional stop datetime (UTC) for the backtest run.
            :param fill_model: The optional fill model change for the backtest run (if None will use previous).
            :param strategies: The optional strategies change for the backtest run (if None will use previous).
            :param print_log_store: If the l

In [13]:
engine.run()

2020-01-17 04:30:30.653Z [INF] BacktestEngine: #---------------------------------------------------------------#
2020-01-17 04:30:30.653Z [INF] BacktestEngine: #----------------------- BACKTEST RUN --------------------------#
2020-01-17 04:30:30.653Z [INF] BacktestEngine: #---------------------------------------------------------------#
2020-01-17 04:30:30.653Z [INF] BacktestEngine: Run started:    2020-01-17 04:30:30.653Z
2020-01-17 04:30:30.653Z [INF] BacktestEngine: Backtest start: 2017-01-03 00:00:00.014Z
2020-01-17 04:30:30.653Z [INF] BacktestEngine: Backtest stop:  2017-11-30 23:59:57.933Z
2020-01-17 04:30:30.653Z [INF] BacktestEngine: Execution resolutions: ['AUDUSD.FXCM=TICK']
2020-01-17 04:30:30.653Z [INF] BacktestEngine: Account balance (starting): 1,000,000.00 USD
2020-01-17 04:30:30.653Z [INF] BacktestEngine: #---------------------------------------------------------------#
2020-01-17 04:30:30.653Z [INF] BacktestEngine: Setting up backtest...
2017-01-03 00:00:00.014Z [INF] 

2017-01-03 02:00:31.365Z [INF] EMACrossPy-AUDUSD: [CMD]--> SubmitAtomicOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, strategy_id=EMACrossPy-AUDUSD, position_id=P-20170103-020031-000-AUDUSD-16, order_id=AO-20170103-020031-000-AUDUSD-46).
2017-01-03 02:00:31.365Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderSubmitted(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-020031-000-AUDUSD-46).
2017-01-03 02:00:31.365Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderAccepted(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-020031-000-AUDUSD-46, label=).
2017-01-03 02:00:31.365Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderWorking(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-020031-000-AUDUSD-46, label=None, BUY 1,510,000 AUDUSD.FXCM STOP_MARKET @ 0.72188 GTD 2017-01-03 02:01:31.365Z).
2017-01-03 02:01:31.431Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderExpired(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-020031-000-AUDUSD-46).
2017-01-03 02:01:39.433Z [INF] EMACrossPy

2017-01-03 06:15:58.076Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-054300-000-AUDUSD-140, quantity=2,220,000, price=0.72319).
2017-01-03 06:15:58.076Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-054300-000-AUDUSD-140, quantity=2,220,000, price=0.72319).
2017-01-03 06:18:53.353Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-054300-000-AUDUSD-140, quantity=2,220,000, price=0.72318).
2017-01-03 06:18:53.353Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-054300-000-AUDUSD-140, quantity=2,220,000, price=0.72318).
2017-01-03 06:33:38.035Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderFilled(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-054300-000-AUDUSD-140, symbol=AUDUSD.FXCM, side=BUY, quantity=2,220,000, avg_p

2017-01-03 08:25:06.604Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-082039-000-AUDUSD-209, quantity=1,820,000, price=0.72155).
2017-01-03 08:25:06.604Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-082039-000-AUDUSD-209, quantity=1,820,000, price=0.72155).
2017-01-03 08:26:04.018Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-082039-000-AUDUSD-209, quantity=1,820,000, price=0.72152).
2017-01-03 08:26:04.018Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-082039-000-AUDUSD-209, quantity=1,820,000, price=0.72152).
2017-01-03 08:33:10.456Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderFilled(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-082039-000-AUDUSD-209, symbol=AUDUSD.FXCM, side=BUY, quantity=1,820,000, avg_p

2017-01-03 10:36:40.560Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-102159-000-AUDUSD-269, quantity=1,780,000, price=0.72098).
2017-01-03 10:36:40.560Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-102159-000-AUDUSD-269, quantity=1,780,000, price=0.72098).
2017-01-03 10:39:14.202Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-102159-000-AUDUSD-269, quantity=1,780,000, price=0.72093).
2017-01-03 10:39:14.202Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-102159-000-AUDUSD-269, quantity=1,780,000, price=0.72093).
2017-01-03 10:40:51.370Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170103-102159-000-AUDUSD-269, quantity=1,780,000, price=0.7

...

2017-01-13 02:33:26.343Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderFilled(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-020257-000-AUDUSD-5997, symbol=AUDUSD.FXCM, side=BUY, quantity=1,020,000, avg_price=0.74883 AUD).
2017-01-13 02:33:26.343Z [INF] EMACrossPy-AUDUSD: <--[EVT] PositionClosed(account_id=NAUTILUS-001-SIMULATED, position_id=P-20170113-020257-000-AUDUSD-1999, entry_direction=SELL, duration=0 days 00:30:28.922000, avg_open_price=0.74974 AUD, avg_close_price=0.74883 AUD, realized_points=0.00091, realized_return=0.121%, realized_pnl=928.20 AUD).
2017-01-13 02:33:26.343Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderCancelled(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-020257-000-AUDUSD-5996).
2017-01-13 02:34:04.620Z [INF] EMACrossPy-AUDUSD: [CMD]--> SubmitAtomicOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, strategy_id=EMACrossPy-AUDUSD, position_id=P-20170113-023404-000-AUDUSD-2000, order_id=AO-20170113-023404-000-AUDUSD-5998).
2017-01-13 02:34:

2017-01-13 04:38:25.936Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-043058-000-AUDUSD-6068, quantity=1,600,000, price=0.74818).
2017-01-13 04:38:25.936Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-043058-000-AUDUSD-6068, quantity=1,600,000, price=0.74818).
2017-01-13 04:40:11.971Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-043058-000-AUDUSD-6068, quantity=1,600,000, price=0.74822).
2017-01-13 04:40:11.971Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-043058-000-AUDUSD-6068, quantity=1,600,000, price=0.74822).
2017-01-13 04:45:48.812Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-043058-000-AUDUSD-6068, quantity=1,600,000, pric

2017-01-13 07:02:17.864Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-065837-000-AUDUSD-6098, quantity=1,660,000, price=0.74974).
2017-01-13 07:02:17.864Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-065837-000-AUDUSD-6098, quantity=1,660,000, price=0.74974).
2017-01-13 07:08:12.108Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-065837-000-AUDUSD-6098, quantity=1,660,000, price=0.74967).
2017-01-13 07:08:12.108Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-065837-000-AUDUSD-6098, quantity=1,660,000, price=0.74967).
2017-01-13 07:18:01.439Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-065837-000-AUDUSD-6098, quantity=1,660,000, pric

2017-01-13 08:35:07.024Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-082851-000-AUDUSD-6134, quantity=1,780,000, price=0.75009).
2017-01-13 08:35:07.024Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-082851-000-AUDUSD-6134, quantity=1,780,000, price=0.75009).
2017-01-13 08:35:48.733Z [INF] EMACrossPy-AUDUSD: [CMD]--> ModifyOrder(trader_id=BACKTESTER-000, account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-082851-000-AUDUSD-6134, quantity=1,780,000, price=0.74990).
2017-01-13 08:35:48.733Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderModified(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-082851-000-AUDUSD-6134, quantity=1,780,000, price=0.74990).
2017-01-13 08:35:55.875Z [INF] EMACrossPy-AUDUSD: <--[EVT] OrderFilled(account_id=NAUTILUS-001-SIMULATED, order_id=O-20170113-082851-000-AUDUSD-6135, symbol=AUDUSD.FXCM, side=BUY, quantity=1,780,000, 

KeyboardInterrupt: 

In [ ]:
engine.trader.generate_account_report()

In [ ]:
engine.trader.generate_order_fills_report()

In [ ]:
engine.trader.generate_positions_report()